In [16]:
import pandas as pd
import csv
import spacy
import string
from nltk.tokenize import word_tokenize
import time
import pickle
from pathlib import Path
from glob import glob
from torchvision import transforms
import cv2
import numpy as np
import torch
import os

In [17]:
df=pd.read_csv("./labelData/RWTH/train.corpus.csv",sep="|")

In [18]:
df.head(10)

id  \
0       01April_2010_Thursday_heute_default-0   
1       01April_2010_Thursday_heute_default-2   
2       01April_2010_Thursday_heute_default-3   
3       01April_2010_Thursday_heute_default-4   
4       01April_2010_Thursday_heute_default-6   
5       01April_2010_Thursday_heute_default-7   
6       01April_2010_Thursday_heute_default-8   
7  01April_2010_Thursday_tagesschau_default-0   
8  01April_2010_Thursday_tagesschau_default-2   
9  01April_2010_Thursday_tagesschau_default-3   

                                              folder    signer  \
0      01April_2010_Thursday_heute_default-0/1/*.png  Signer04   
1      01April_2010_Thursday_heute_default-2/1/*.png  Signer04   
2      01April_2010_Thursday_heute_default-3/1/*.png  Signer04   
3      01April_2010_Thursday_heute_default-4/1/*.png  Signer04   
4      01April_2010_Thursday_heute_default-6/1/*.png  Signer04   
5      01April_2010_Thursday_heute_default-7/1/*.png  Signer04   
6      01April_2010_Thursday_heute_default-8/1/*.png  Signer04   
7  01April_2010_Thursday_tagesschau_default-0/1/*...  Signer04   
8  01April_2010_Thursday_tagesschau_default-2/1/*...  Signer04   
9  01April_2010_Thursday_tagesschau_default-3/1/*...  Signer04   

                                          annotation  
0  __ON__ LIEB ZUSCHAUER ABEND WINTER GESTERN loc...  
1               loc-WEST WARM loc-WEST BLEIBEN KUEHL  
2  KUEHL KUEHL IN-KOMMEND NACHT MINUS loc-MINUS-P...  
3  MORGEN TEMPERATUR ACHT BIS DREIZEHN MAXIMAL DR...  
4  AUCH SAMSTAG WEST FREUNDLICH IX TROCKEN WEST R...  
5  SONNTAG SUED SCHNEE DABEI MONTAG __EMOTION__ S...  
6  DANN FREUNDLICH KLAR MONTAG MEHR MEHR WARM AB ...  
7  __ON__ WETTER WIE-AUSSEHEN MORGEN FREITAG ZWEI...  
8  HEUTE NACHT OST REGEN loc-NORD __EMOTION__ REG...  
9  IX SCHAUER ABEND WEST loc-SUED BISSCHEN REGEN ...

In [19]:
for row in df.loc[:,"annotation"]:
    print(row.split())

['__ON__', 'LIEB', 'ZUSCHAUER', 'ABEND', 'WINTER', 'GESTERN', 'loc-NORD', 'SCHOTTLAND', 'loc-REGION', 'UEBERSCHWEMMUNG', 'AMERIKA', 'IX']
['loc-WEST', 'WARM', 'loc-WEST', 'BLEIBEN', 'KUEHL']
['KUEHL', 'KUEHL', 'IN-KOMMEND', 'NACHT', 'MINUS', 'loc-MINUS-PLUSPLUS', 'TEIL', 'MINUS', 'FUENF', 'ALPEN', 'KUESTE', 'NULL']
['MORGEN', 'TEMPERATUR', 'ACHT', 'BIS', 'DREIZEHN', 'MAXIMAL', 'DREIZEHN']
['AUCH', 'SAMSTAG', 'WEST', 'FREUNDLICH', 'IX', 'TROCKEN', 'WEST', 'REGEN', 'REGEN']
['SONNTAG', 'SUED', 'SCHNEE', 'DABEI', 'MONTAG', '__EMOTION__', 'SCHAUER', 'KOMMEN']
['DANN', 'FREUNDLICH', 'KLAR', 'MONTAG', 'MEHR', 'MEHR', 'WARM', 'AB', 'DIENSTAG', 'JETZT', 'WUENSCHEN', 'SCHOEN', 'ABEND', '__OFF__']
['__ON__', 'WETTER', 'WIE-AUSSEHEN', 'MORGEN', 'FREITAG', 'ZWEITE', 'APRIL', '__OFF__']
['HEUTE', 'NACHT', 'OST', 'REGEN', 'loc-NORD', '__EMOTION__', 'REGEN-PLUSPLUS', 'MORGEN', 'UEBERWIEGEND', 'FREUNDLICH']
['IX', 'SCHAUER', 'ABEND', 'WEST', 'loc-SUED', 'BISSCHEN', 'REGEN', 'REGEN']
['HIER', 'WIND', '

In [20]:
df.iloc[0,:].values

array(['01April_2010_Thursday_heute_default-0',
       '01April_2010_Thursday_heute_default-0/1/*.png', 'Signer04',
       '__ON__ LIEB ZUSCHAUER ABEND WINTER GESTERN loc-NORD SCHOTTLAND loc-REGION UEBERSCHWEMMUNG AMERIKA IX'],
      dtype=object)

In [21]:
len(df.iloc[:,3].values)

5672

In [22]:
type(df.iloc[:,3].values)

numpy.ndarray

In [23]:
label_dict=dict(zip(df.loc[:,"id"].values,df.loc[:,"annotation"].values))

In [24]:
label_dict

{'01April_2010_Thursday_heute_default-0': '__ON__ LIEB ZUSCHAUER ABEND WINTER GESTERN loc-NORD SCHOTTLAND loc-REGION UEBERSCHWEMMUNG AMERIKA IX',
 '01April_2010_Thursday_heute_default-2': 'loc-WEST WARM loc-WEST BLEIBEN KUEHL',
 '01April_2010_Thursday_heute_default-3': 'KUEHL KUEHL IN-KOMMEND NACHT MINUS loc-MINUS-PLUSPLUS TEIL MINUS FUENF ALPEN KUESTE NULL',
 '01April_2010_Thursday_heute_default-4': 'MORGEN TEMPERATUR ACHT BIS DREIZEHN MAXIMAL DREIZEHN',
 '01April_2010_Thursday_heute_default-6': 'AUCH SAMSTAG WEST FREUNDLICH IX TROCKEN WEST REGEN REGEN',
 '01April_2010_Thursday_heute_default-7': 'SONNTAG SUED SCHNEE DABEI MONTAG __EMOTION__ SCHAUER KOMMEN',
 '01April_2010_Thursday_heute_default-8': 'DANN FREUNDLICH KLAR MONTAG MEHR MEHR WARM AB DIENSTAG JETZT WUENSCHEN SCHOEN ABEND __OFF__',
 '01April_2010_Thursday_tagesschau_default-0': '__ON__ WETTER WIE-AUSSEHEN MORGEN FREITAG ZWEITE APRIL __OFF__',
 '01April_2010_Thursday_tagesschau_default-2': 'HEUTE NACHT OST REGEN loc-NORD __EM

In [25]:
for id in label_dict.keys():
    print(id)

01April_2010_Thursday_heute_default-0
01April_2010_Thursday_heute_default-2
01April_2010_Thursday_heute_default-3
01April_2010_Thursday_heute_default-4
01April_2010_Thursday_heute_default-6
01April_2010_Thursday_heute_default-7
01April_2010_Thursday_heute_default-8
01April_2010_Thursday_tagesschau_default-0
01April_2010_Thursday_tagesschau_default-2
01April_2010_Thursday_tagesschau_default-3
01April_2010_Thursday_tagesschau_default-4
01April_2010_Thursday_tagesschau_default-5
01April_2010_Thursday_tagesschau_default-6
01April_2010_Thursday_tagesschau_default-9
01April_2011_Friday_tagesschau_default-2
01April_2011_Friday_tagesschau_default-4
01April_2011_Friday_tagesschau_default-7
01April_2011_Friday_tagesschau_default-9
01April_2011_Friday_tagesschau_default-10
01April_2011_Friday_tagesschau_default-11
01April_2011_Friday_tagesschau_default-12
01April_2011_Friday_tagesschau_default-13
01August_2011_Monday_heute_default-0
01August_2011_Monday_heute_default-1
01August_2011_Monday_heute_

In [26]:
df=pd.read_csv("./labelData/CE-CSL/train.csv",sep=",")

In [27]:
for gloss in df.loc[:,"Gloss"]:
    print(gloss.split("/"))

['2', '0', '2', '3', '高', '考', '时间', '到', '。']
['小时', '时间', '我', '意思', '她', '明白', '。']
['小', '生命', '到', '家', '大', '快乐', '给', '可以', '。']
['美', '女', '一', '。']
['困难', '挑战', '忽视', '不行', '。']
['学生', '这', '贫困', '学校', '退1', '。']
['这', '方面', '帮助', '给', '。']
['一会儿', '去', '可以', '。']
['开始', '一直', '要', '。']
['分钟', '后2', '去', '上班2', '要', '。']
['都', '辛苦', '价值', '。']
['都', '经过', '会', '。']
['都', '好', '方向', '发展', '会', '。']
['都', '计划', '按照', '发展', '是', '。']
['都', '心', '顺利', '好', '。']
['表情', '无力', '。']
['香烟', '价格', '部分', '三', '。']
['大', '茂盛', '法国', '花', '名字', '吊兰', '。']
['一定1', '做', '到', '可以', '。']
['一定1', '分钟', '三', '刷', '要', '。']
['一定1', '身体', '保养', '好', '要', '。']
['一年', '内', '用', '可以', '。']
['行李', '找', '有', '快', '我', '饭店', '给', '。']
['书', '哪里', '开始', '都', '吸引', '会', '。']
['地震', '让', '城市', '都', '塌陷', '。']
['声音', '都', '没有', '。']
['属于1', '时间', '没有', '。']
['上', '火', '不', '。']
['一直', '说话', '没有', '。']
['一般', '打折', '票', '用', '商品', '价格', '打折', '票', '多少', '扣除', '。']
['一般', '飞机', '书包', '最2', '大', '二', '公斤', '。'

In [28]:
with open("./labelData/RWTH-T/PHOENIX-2014-T.train.corpus.csv",mode="r",encoding="utf-8") as file:
    reader=csv.reader(file)
    for index,row in enumerate(reader):
        if index!=0:
            row_str_list=row[0].split("|")[5].split()
            for word in row_str_list:
                if word in string.punctuation:
                    print(row_str_list)
                    break

In [29]:
nlp = spacy.load("en_core_web_md")

In [30]:
start=time.time()
with open("./labelData/RWTH-T/PHOENIX-2014-T.train.corpus.csv",mode="r",encoding="utf-8") as file:
    reader=csv.reader(file)
    for index,row in enumerate(reader):
        if index!=0:
            row_str_list=word_tokenize(row[0].split("|")[5])
            for word in row_str_list:
                if word in string.punctuation:
                    print(row_str_list)
                    break
need_time=time.time()-start
print(need_time)

0.3478670120239258


In [31]:
with open("./labelData/CSL-Daily/csl2020ct_v2.pkl", 'rb') as f:
        data = pickle.load(f)
        wordList = data["gloss_map"]

In [32]:
wordList

['0',
 '1',
 '11',
 '12',
 '15',
 '18',
 '2',
 '20',
 '24',
 '3',
 '30',
 '32',
 '4',
 '45',
 '5',
 '50',
 '500',
 '6',
 '7',
 '70',
 '75',
 '8',
 '9',
 '98',
 'APP',
 'P',
 'PPT',
 '爱',
 '癌',
 '爱-1',
 '爱好',
 '爱护',
 '爱情',
 '艾滋',
 '按',
 '安',
 '暗',
 '按键',
 '安静',
 '安排',
 '安全',
 '安全套',
 '安慰',
 '按照',
 '安装',
 '奥运',
 '阿姨',
 'b',
 '把',
 '爸爸',
 '八宝粥',
 '白',
 '百',
 '白内障',
 '白天',
 '班',
 '办',
 '半',
 '搬',
 '版',
 '办公室',
 '榜样',
 '帮助',
 '班级',
 '办理',
 '斑马',
 '斑马线',
 '班长',
 '包',
 '饱',
 '抱',
 '薄',
 '报',
 '宝宝',
 '包庇',
 '保持',
 '报复',
 '报告',
 '宝贵',
 '保护',
 '包括',
 '保密',
 '报名',
 '保险',
 '保养',
 '抱怨',
 '爆炸',
 '保证',
 '报纸',
 '包装',
 '把握',
 '北',
 '被',
 '卑',
 '辈',
 '背后',
 '北京',
 '贝壳',
 '杯子',
 '被子',
 '本',
 '笨',
 '奔驰',
 '绷带',
 '本领',
 '比',
 '笔',
 '逼',
 '变',
 '边',
 '变化',
 '表',
 '表白',
 '表格',
 '表面',
 '表情',
 '表示',
 '表现',
 '表扬',
 '标志',
 '标准',
 '别',
 '别人',
 '比较',
 '笔记本',
 '避免',
 '病',
 '兵',
 '病毒',
 '病历',
 '宾馆',
 '冰箱',
 '比如',
 '比赛',
 '必须',
 '毕业',
 '避孕',
 '闭嘴',
 '伯伯',
 '播放',
 '玻璃',
 '博物',
 '不',
 '部',
 '步',
 '布',
 '不懂',
 '部分',
 '不

In [33]:
folder=Path("./data/video/dev/A/dev-00001")
for path in folder.glob("*"):
    print(path.name)

00000.jpg
00001.jpg
00002.jpg
00003.jpg
00004.jpg
00005.jpg
00006.jpg
00007.jpg
00008.jpg
00009.jpg
00010.jpg
00011.jpg
00012.jpg
00013.jpg
00014.jpg
00015.jpg
00016.jpg
00017.jpg
00018.jpg
00019.jpg
00020.jpg
00021.jpg
00022.jpg
00023.jpg
00024.jpg
00025.jpg
00026.jpg
00027.jpg
00028.jpg
00029.jpg
00030.jpg
00031.jpg
00032.jpg
00033.jpg
00034.jpg
00035.jpg
00036.jpg
00037.jpg
00038.jpg
00039.jpg
00040.jpg
00041.jpg
00042.jpg
00043.jpg
00044.jpg
00045.jpg
00046.jpg
00047.jpg
00048.jpg
00049.jpg
00050.jpg
00051.jpg
00052.jpg
00053.jpg
00054.jpg
00055.jpg
00056.jpg
00057.jpg
00058.jpg
00059.jpg
00060.jpg
00061.jpg
00062.jpg
00063.jpg
00064.jpg
00065.jpg
00066.jpg
00067.jpg
00068.jpg
00069.jpg
00070.jpg
00071.jpg
00072.jpg
00073.jpg
00074.jpg
00075.jpg
00076.jpg
00077.jpg
00078.jpg
00079.jpg
00080.jpg
00081.jpg
00082.jpg
00083.jpg
00084.jpg
00085.jpg
00086.jpg
00087.jpg
00088.jpg
00089.jpg
00090.jpg
00091.jpg
00092.jpg
00093.jpg
00094.jpg
00095.jpg
00096.jpg
00097.jpg
00098.jpg
00099.jpg


In [34]:
images=glob("./data/video/dev/A/dev-00001/*")

In [35]:
images

['./data/video/dev/A/dev-00001/00000.jpg',
 './data/video/dev/A/dev-00001/00001.jpg',
 './data/video/dev/A/dev-00001/00002.jpg',
 './data/video/dev/A/dev-00001/00003.jpg',
 './data/video/dev/A/dev-00001/00004.jpg',
 './data/video/dev/A/dev-00001/00005.jpg',
 './data/video/dev/A/dev-00001/00006.jpg',
 './data/video/dev/A/dev-00001/00007.jpg',
 './data/video/dev/A/dev-00001/00008.jpg',
 './data/video/dev/A/dev-00001/00009.jpg',
 './data/video/dev/A/dev-00001/00010.jpg',
 './data/video/dev/A/dev-00001/00011.jpg',
 './data/video/dev/A/dev-00001/00012.jpg',
 './data/video/dev/A/dev-00001/00013.jpg',
 './data/video/dev/A/dev-00001/00014.jpg',
 './data/video/dev/A/dev-00001/00015.jpg',
 './data/video/dev/A/dev-00001/00016.jpg',
 './data/video/dev/A/dev-00001/00017.jpg',
 './data/video/dev/A/dev-00001/00018.jpg',
 './data/video/dev/A/dev-00001/00019.jpg',
 './data/video/dev/A/dev-00001/00020.jpg',
 './data/video/dev/A/dev-00001/00021.jpg',
 './data/video/dev/A/dev-00001/00022.jpg',
 './data/vi

In [36]:
print(len(images))

236


In [37]:
images[0]

'./data/video/dev/A/dev-00001/00000.jpg'

In [38]:
sample_images=[images[index] for index in range(10)]
image_arrays=np.array([cv2.resize(cv2.cvtColor(cv2.imread(image),code=cv2.COLOR_BGR2RGB),dsize=(256,256)) for image in sample_images])

In [39]:
image_arrays.shape

(10, 256, 256, 3)

In [40]:
for image in image_arrays:
    image=transforms.ToTensor()(image)
    print(image.shape)

torch.Size([3, 256, 256])
torch.Size([3, 256, 256])
torch.Size([3, 256, 256])
torch.Size([3, 256, 256])
torch.Size([3, 256, 256])
torch.Size([3, 256, 256])
torch.Size([3, 256, 256])
torch.Size([3, 256, 256])
torch.Size([3, 256, 256])
torch.Size([3, 256, 256])


In [41]:
os.path.basename("./data/video/dev/A/dev-00001")

'dev-00001'

In [42]:
df=pd.read_csv("./labelData/RWTH-T/PHOENIX-2014-T.train.corpus.csv",sep="|")
data=df.head(10)

In [43]:
label_dict=dict()
for name,orth in zip(data.iloc[:,0],data.iloc[:,-2]):
    label_dict[name]=orth

In [44]:
label_dict

{'11August_2010_Wednesday_tagesschau-1': 'JETZT WETTER MORGEN DONNERSTAG ZWOELF FEBRUAR',
 '11August_2010_Wednesday_tagesschau-4': 'ORT REGEN DURCH REGEN KOENNEN UEBERSCHWEMMUNG KOENNEN',
 '11August_2010_Wednesday_tagesschau-5': 'NORDWEST HEUTE NACHT TROCKEN BLEIBEN SUEDWEST KOENNEN REGEN ORT GEWITTER DAZU',
 '11August_2010_Wednesday_tagesschau-6': 'TAGSUEBER OFT REGEN GEWITTER KOENNEN MANCHMAL REGEN VIEL REGEN',
 '11August_2010_Wednesday_tagesschau-7': 'WOLKE LOCH SPEZIELL NORDWEST',
 '11August_2010_Wednesday_tagesschau-9': 'FLUSS HEUTE NACHT SECHS FLUSS SIEBZEHN GRAD',
 '11August_2010_Wednesday_tagesschau-10': 'MORGEN TEMPERATUR GLEICH-WIE HEUTE NEUNZEHN BIS FUENF ZWANZIG L IX SIEBEN ZWANZIG GRAD',
 '11August_2010_Wednesday_tagesschau-11': 'FREITAG OST KOENNEN REGEN STARK REGEN VORSICHT UEBERSCHWEMMUNG KOENNEN',
 '11August_2010_Wednesday_tagesschau-12': 'REGION WECHSELHAFT REGEN GEWITTER AUCH WOCHENENDE',
 '11August_2010_Wednesday_tagesschau-13': 'TEMPERATUR BLEIBEN GLEICH'}

In [45]:
import config
with open("./labelData/CSL-Daily/csl2020ct_v2.pkl","rb") as file:
    data=pickle.load(file)
data=data["info"]

In [46]:
for item in data:
    gloss=item.get("label_gloss")
    name=item.get("name")
    print(gloss)
    print(name)

['你们', '好']
S000000_P0000_T00
['你们', '好']
S000000_P0004_T00
['你们', '好']
S000000_P0008_T00
['对不起']
S000001_P0000_T00
['对不起']
S000001_P0004_T00
['对不起']
S000001_P0008_T00
['没关系']
S000002_P0000_T00
['没关系']
S000002_P0004_T00
['没关系']
S000002_P0008_T00
['谢谢']
S000003_P0000_T00
['谢谢']
S000003_P0004_T00
['谢谢']
S000003_P0008_T00
['礼貌', '不']
S000004_P0000_T00
['礼貌', '不']
S000004_P0004_T00
['礼貌', '不']
S000004_P0008_T00
['你', '名字', '什么']
S000005_P0000_T00
['你', '名字', '什么']
S000005_P0008_T00
['我', '名字', '孩子']
S000006_P0000_T00
['我', '名字', '孩子']
S000006_P0004_T00
['我', '名字', '孩子']
S000006_P0008_T00
['他', '谁']
S000007_P0000_T00
['他', '谁']
S000007_P0003_T00
['他', '谁']
S000007_P0004_T00
['他', '谁']
S000007_P0008_T00
['他', '我', '手语', '老师']
S000008_P0000_T00
['他', '我', '手语', '老师']
S000008_P0004_T00
['你', '老师', '是']
S000009_P0000_T00
['你', '老师', '是']
S000009_P0008_T00
['我', '老师', '不是', '学生', '是']
S000010_P0000_T00
['我', '老师', '不是', '学生', '是']
S000010_P0004_T00
['我', '老师', '不是', '学生', '是']
S000010_P0008_T00


In [47]:
df=pd.read_csv("./labelData/CSL-Daily/train.txt",header=None,names=["dir_name","kind"])
df

dir_name  kind
0      S000000_P0000_T00|train   NaN
1      S000000_P0004_T00|train   NaN
2      S000000_P0008_T00|train   NaN
3      S000001_P0000_T00|train   NaN
4      S000001_P0004_T00|train   NaN
...                        ...   ...
18396  S007410_P0003_T00|train   NaN
18397  S007410_P0007_T00|train   NaN
18398  S007411_P0000_T00|train   NaN
18399  S007411_P0003_T00|train   NaN
18400  S007411_P0007_T00|train   NaN

[18401 rows x 2 columns]

In [48]:
for image_seq_name in df["dir_name"]:
    print(image_seq_name)

S000000_P0000_T00|train
S000000_P0004_T00|train
S000000_P0008_T00|train
S000001_P0000_T00|train
S000001_P0004_T00|train
S000001_P0008_T00|train
S000002_P0000_T00|train
S000002_P0004_T00|train
S000002_P0008_T00|train
S000003_P0000_T00|train
S000003_P0004_T00|train
S000003_P0008_T00|train
S000004_P0000_T00|train
S000004_P0004_T00|train
S000004_P0008_T00|train
S000005_P0000_T00|train
S000005_P0004_T00|train
S000005_P0008_T00|train
S000006_P0000_T00|train
S000006_P0004_T00|train
S000006_P0008_T00|train
S000007_P0000_T00|train
S000007_P0004_T00|train
S000007_P0008_T00|train
S000008_P0000_T00|train
S000008_P0004_T00|train
S000009_P0000_T00|train
S000009_P0008_T00|train
S000010_P0000_T00|train
S000010_P0004_T00|train
S000010_P0008_T00|train
S000011_P0000_T00|train
S000011_P0004_T00|train
S000011_P0008_T00|train
S000012_P0000_T00|train
S000012_P0004_T00|train
S000012_P0008_T00|train
S000013_P0000_T00|train
S000013_P0004_T00|train
S000013_P0008_T00|train
S000014_P0000_T00|train
S000014_P0004_T0

In [49]:
class Nihao:
    key="lihua"
    def hi(self):
        print(f"Hi {self.key}!")

In [50]:
lihua=Nihao()
lihua.hi()

Hi lihua!


In [51]:
from collections import defaultdict
from loguru import logger
# 定义默认字典
class custom_defaultdict(defaultdict):
    def __init__(self,*args,**kwargs):
        super().__init__(*args,**kwargs) # 继承父类
        self.warned=set()
        self.warning_enabled=False
    def __getitem__(self,key):
        if key=="text" and key not in self.warned and self.warning_enabled:
            logger.warning(f"The batch['tetx'] is no longer in use, please replace it with a batch['label'].")
            self.warned.add(key)
        return super().__getitem__(key)

In [52]:
custom_dict=custom_defaultdict(list)
custom_dict["text"]
custom_dict.warning_enabled=True
custom_dict["text"]

2025-10-14 13:09:43.963 | WARNING  | __main__:__getitem__:11 - The batch['tetx'] is no longer in use, please replace it with a batch['label'].


[]

In [53]:
a=["lisisi","liliu","liuxiao"]
b=list(sorted(a,key=lambda x:len(x),reverse=True))
b

['liuxiao', 'lisisi', 'liliu']

In [54]:
c=list(i for i in range(10))
c

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9]

In [67]:
c=np.ones(shape=(10,))
c

array([1., 1., 1., 1., 1., 1., 1., 1., 1., 1.])